<a href="https://colab.research.google.com/github/gizdatalab/SGD_11_Tracking_Colombia/blob/main/OSM_City.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
%%capture
!pip install geopandas
!pip install folium
!pip install geemap

# Classify Public spaces from OSM using Overpass API
https://wiki.openstreetmap.org/wiki/Overpass_API

In [2]:
from shapely.geometry import shape, Point, Polygon
import geopandas as gpd
import pandas as pd

def to_geom(x):
    if len(x)>2:
        y = Polygon([(pair['lon'],pair['lat']) for pair in x])
    else:
        y = Point(x[0]['lat'],x[0]['lon'])
    return y

def to_gdf(df):
    df['geometry'] = df['geometry'].apply(lambda x: shape(to_geom(x)))
    gdf = gpd.GeoDataFrame(df, geometry=df.geometry)

    gdf = gdf.set_crs(epsg=4326)#, inplace=True) 4326 3857
    gdf['area'] = gdf['geometry'].area * 100000
    return gdf


def explode(indata):
    outdf = pd.DataFrame(columns=indata.columns)
    outdf['geometry'] = None
    for idx, row in indata.iterrows():
        for pol in row['members']:
            row['geometry'] = to_geom(pol['geometry'])
            outdf = outdf.append(row,ignore_index=True)
            
            #print(idx,pol['geometry'])
    gdf_out = gpd.GeoDataFrame(outdf, geometry=outdf.geometry)
    gdf_out = gdf_out.set_crs(epsg=4326)#, inplace=True) 4326 3857
    gdf_out['area'] = gdf_out['geometry'].area * 100000
    return gdf_out


## Landuse filter


Landuse | frequency
--- | ---
residential         |       1909  
forest               |       274  
grass                |       215  
farmland             |        70  
industrial           |        56  
garages              |        44  
recreation_ground    |        43  
orchard              |        37  
commercial           |        32  
meadow               |        21  
retail               |        13  
greenfield           |        12  
religious            |        11  
construction         |        10  

In [3]:
from pandas.io.json import json_normalize
import requests

url = 'http://overpass-api.de/api/interpreter'  # Overpass API URL

query = f"""
    [out:json];
    area["name"="Medellín"][admin_level=6];
    way["landuse"~"^(forest|grass|water|recreation_ground)$"](area) ;   
    out geom;
"""
r = requests.get(url, params={'data': query})
data = r.json()['elements']  # read response as JSON and get the data
df_lu = json_normalize(data)  # create a DataFrame from the data
print(df_lu.shape)
df_lu[:3]

(547, 27)


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:14: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  


type        id  ... tags.barrier tags.access
0  way  28565409  ...          NaN         NaN
1  way  29640187  ...          NaN         NaN
2  way  30011584  ...          NaN         NaN

[3 rows x 27 columns]

In [4]:
gdf_lu = to_gdf(df_lu)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:17: UserWarning: Geometry is in a geographic CRS. Results from 'area' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



In [23]:
gdf_lu['building'] = False
gdf_lu['info1'] = gdf_lu['tags.landuse']
gdf_lu['info2'] = gdf_lu['tags.leisure']
gdf_lu['info3'] = gdf_lu['id']

Multipoly

In [6]:
from pandas.io.json import json_normalize
import requests

url = 'http://overpass-api.de/api/interpreter'  # Overpass API URL

query = f"""
    [out:json];
    area["name"="Medellín"][admin_level=6];
    //way["landuse"~"^(forest|grass|water|recreation_ground)$"](area);
    relation["landuse"~"^(forest|grass|water|recreation_ground)$"](area) ;   
    out geom;
"""
r = requests.get(url, params={'data': query})
data = r.json()['elements']  # read response as JSON and get the data
df_lu2 = json_normalize(data)  # create a DataFrame from the data
print(df_lu2.shape)
df_lu2[:3]

(8, 22)


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:15: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  from ipykernel import kernelapp as app


type       id  ... tags.designation  tags.source
0  relation  5423166  ...              NaN          NaN
1  relation  5489364  ...              NaN          NaN
2  relation  5490813  ...              NaN          NaN

[3 rows x 22 columns]

In [7]:
gdf_lu2 = explode(df_lu2)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:32: UserWarning: Geometry is in a geographic CRS. Results from 'area' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



In [24]:
gdf_lu2['building'] = False
gdf_lu2['info1'] = gdf_lu2['tags.landuse']
gdf_lu2['info2'] = gdf_lu2['tags.type']
gdf_lu2['info3'] = gdf_lu2['id']

In [9]:
import folium

style0 = {'fillColor': '#ffffff', 'color': '#ffffff'}
style1 = {'fillColor': '#202c3d', 'color': '#202c3d'}

m = folium.Map([6.2,-75.6], zoom_start=12)
folium.GeoJson(gdf_lu2,style_function=lambda x:style1,tooltip=folium.features.GeoJsonTooltip (fields=['tags.type','tags.landuse','id','type','area'])).add_to(m)

m

## Natural Filter

Landuse | frequency
--- | ---
wood     |    601
tree_row  |   169
water      |   68
sand        |  65
grassland    | 54
scrub         |51

In [10]:
url = 'http://overpass-api.de/api/interpreter'  # Overpass API URL

query = f"""
    [out:json];
    area["name"="Medellín"][admin_level=6];
    way["natural"~"^(wood|tree_row|water|sand|grassland|scrub)$"](area) ;   
    out geom;
"""

r = requests.get(url, params={'data': query})
data = r.json()['elements']  # read response as JSON and get the data
df_nat = json_normalize(data)  # create a DataFrame from the data
print(df_nat.shape)
df_nat[:3]

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:12: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  if sys.path[0] == '':


(1008, 24)


type        id  ... tags.opening_hours tags.tourism
0  way  31016875  ...                NaN          NaN
1  way  31898314  ...                NaN          NaN
2  way  37017542  ...                NaN          NaN

[3 rows x 24 columns]

In [11]:
gdf_nat = to_gdf(df_nat)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:17: UserWarning: Geometry is in a geographic CRS. Results from 'area' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



In [35]:
gdf_nat['building'] = False
gdf_nat['info1'] = gdf_nat['tags.natural']
gdf_nat['info2'] = gdf_nat['tags.leisure']
gdf_nat['info3'] = gdf_nat['id']

## Filter Leisure

Landuse | frequency
--- | ---
park     |            720
pitch     |           621
swimming_pool|        299
garden        |        54
playground    |        53
sports_centre |        43
fitness_centre |       13
fitness_station |      11
track            |      8
common           |      6
stadium          |      5

In [13]:
url = 'http://overpass-api.de/api/interpreter'  # Overpass API URL

query = f"""
    [out:json];
    area["name"="Medellín"][admin_level=6];
    way["leisure"~"^(park|garden|playground|sports_centre|fitness_station)$"](area) ;   
    out geom;
"""

r = requests.get(url, params={'data': query})
data = r.json()['elements']  # read response as JSON and get the data
df_lei = json_normalize(data)  # create a DataFrame from the data
print(df_lei.shape)
df_lei[:3]

(881, 48)


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:12: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  if sys.path[0] == '':


type        id  ... tags.note tags.opening_hours:covid19
0  way  28565409  ...       NaN                        NaN
1  way  28565493  ...       NaN                        NaN
2  way  28565538  ...       NaN                        NaN

[3 rows x 48 columns]

In [14]:
df_lei['tags.building'].value_counts()

yes           14
public         2
University     1
university     1
Name: tags.building, dtype: int64

In [15]:
gdf_lei = to_gdf(df_lei)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:17: UserWarning: Geometry is in a geographic CRS. Results from 'area' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



In [22]:
gdf_lei['building'] = gdf_lei['tags.building'].isna()==False
gdf_lei['info1'] = gdf_lei['tags.landuse']
gdf_lei['info2'] = gdf_lei['tags.leisure']
gdf_lei['info3'] = gdf_lei['id']

In [ ]:
import folium

style0 = {'fillColor': '#ffffff', 'color': '#ffffff'}
style1 = {'fillColor': '#202c3d', 'color': '#202c3d'}

m = folium.Map([6.2,-75.6], zoom_start=12)
folium.GeoJson(gdf_lei[gdf_lei['tags.leisure']=='garden'],style_function=lambda x:style1,tooltip=folium.features.GeoJsonTooltip (fields=['tags.leisure','tags.natural','id','type','area'])).add_to(m)

m

## Filter Amenity

Landuse | frequency
--- | ---
parking      |       286
school        |      208
place_of_worship|    163
fuel       |          86
hospital    |         54
restaurant   |        51
clinic        |       49
college        |      48
community_centre|     46
library          |    40
university        |   27
social_facility    |  22
police              | 22
bank                 v21

In [25]:
url = 'http://overpass-api.de/api/interpreter'  # Overpass API URL

query = f"""
    [out:json];
    area["name"="Medellín"][admin_level=6];
    way["amenity"~"^(school|hospital|college|community_centre|university)$"](area) ;   
    //way["amenity"](area) ;   
    out geom;
"""

r = requests.get(url, params={'data': query})
data = r.json()['elements']  # read response as JSON and get the data
df_am = json_normalize(data)  # create a DataFrame from the data
print(df_am.shape)
df_am[:3]

(383, 54)


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:13: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  del sys.path[0]


type        id  ... tags.opening_hours:covid19 tags.grades
0  way  32774024  ...                        NaN         NaN
1  way  33784057  ...                        NaN         NaN
2  way  44878015  ...                        NaN         NaN

[3 rows x 54 columns]

In [26]:
gdf_am = to_gdf(df_am)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:17: UserWarning: Geometry is in a geographic CRS. Results from 'area' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



In [27]:
gdf_am['building'] = gdf_am['tags.building'].isna()==False
gdf_am['info1'] = gdf_am['tags.amenity']
gdf_am['info2'] = gdf_am['tags.name']
gdf_am['info3'] = gdf_am['id']

In [28]:
import folium

style0 = {'fillColor': '#ffffff', 'color': '#ffffff'}
style1 = {'fillColor': '#202c3d', 'color': '#202c3d'}

m = folium.Map([6.2,-75.6], zoom_start=12)
folium.GeoJson(gdf_am,style_function=lambda x:style1,tooltip=folium.features.GeoJsonTooltip (fields=['tags.amenity','tags.operator','id','type','area'])).add_to(m)

m

## Merge Data

In [29]:
var = ['id','geometry','info1','info2','building']

In [30]:
print(gdf_lu.shape,gdf_lu2.shape,gdf_nat.shape,gdf_lei.shape,gdf_am.shape)

(547, 32) (22, 28) (1008, 28) (881, 53) (383, 59)


In [36]:
gdf_nat[var][:2]

id                                           geometry  ... info2 building
0  31016875  POLYGON ((-75.50283 6.29564, -75.50295 6.29571...  ...   NaN    False
1  31898314  POLYGON ((-75.62820 6.27276, -75.62845 6.27284...  ...   NaN    False

[2 rows x 5 columns]

In [37]:
gdf_all = gdf_lu[var].append(gdf_lu2[var]).append(gdf_nat[var]).append(gdf_lei[var]).append(gdf_am[var])
print(gdf_all.shape)

(2841, 5)


In [38]:
import folium

style0 = {'fillColor': '#ffffff', 'color': '#ffffff'}
style1 = {'fillColor': '#202c3d', 'color': '#202c3d'}

m = folium.Map([6.2,-75.6], zoom_start=12)
folium.GeoJson(gdf_all,style_function=lambda x:style1,tooltip=folium.features.GeoJsonTooltip (fields= ['id','info1','info2'])).add_to(m)

m

In [39]:
gdf_all = gdf_all.drop_duplicates()
print(gdf_all.shape)

(2831, 5)


In [40]:
lt = [geo.type=='Polygon' for geo in gdf_all['geometry']]
gdf_all = gdf_all[lt] #[df['geometry'].type=='Polygon']
print(gdf_all.shape)

(2812, 5)


In [41]:
gdf_all[var].to_file(driver = 'ESRI Shapefile', filename= "medellin_public.shp")

In [42]:
from google.colab import files
files.download('medellin_public.shp') 
files.download('medellin_public.shx') 
files.download('medellin_public.prj') 
files.download('medellin_public.cpg') 
files.download('medellin_public.dbf') 

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
import geemap

# Streets

In [ ]:
from pandas.io.json import json_normalize
import requests

#rel["building"]["type"="multipolygon"](-75.5425500869751,  6.286292383046487, -75.55463075637817,  6.29595417216477);
#area['name'='Medellin']->.medellin;
#way["building"](area.medellin);

url = 'http://overpass-api.de/api/interpreter'  # Overpass API URL


query = f"""
    [out:json];
    area["name"="Medellín"][admin_level=6];
    way["highway"~"^(residential|primary|secondary|tertiary)$"](area) ;
    out geom;
"""

r = requests.get(url, params={'data': query})
data = r.json()['elements']  # read response as JSON and get the data
df_street = json_normalize(data)  # create a DataFrame from the data
print(df_street.shape)
df_street[:3]

In [ ]:
gdf_street = to_gdf(df_street)

In [ ]:
lt = [geo.type=='Polygon' for geo in df['geometry']]
df_street = df_street[lt] #[df['geometry'].type=='Polygon']
print(df_street.shape)

In [ ]:
import folium

style0 = {'fillColor': '#ffffff', 'color': '#ffffff'}
style1 = {'fillColor': '#202c3d', 'color': '#202c3d'}
style2 = {'fillColor': '#488992', 'color': '#488992'}
style3 = {'fillColor': '#e4b04e', 'color': '#e4b04e'}
style4 = {'fillColor': '#da5151', 'color': '#da5151'}

#gdf = gdf[gdf['year']=='2017']

m = folium.Map([y, x], zoom_start=12)
#folium.GeoJson(m_aoi_ucu).add_to(m)
folium.GeoJson(df_street[df_street['area']<0.03][:2000],style_function=lambda x:style1,tooltip=folium.features.GeoJsonTooltip (fields=['tags.highway','tags.name','id','type','area'])).add_to(m)


m

In [ ]:
gdf_street['highway'] = gdf_street['tags.highway']
gdf_street = gdf_street[gdf_street['area']<0.03]

In [ ]:
gdf_all[var].to_file(driver = 'ESRI Shapefile', filename= "medellin_public.shp")

In [ ]:
from google.colab import files
files.download('medellin_public.shp') 
files.download('medellin_public.shx') 
files.download('medellin_public.prj') 
files.download('medellin_public.cpg') 
files.download('medellin_public.dbf') 